In [97]:
import pandas as pd
import numpy as np
import geopandas  as gpd
import altair as alt
from datetime import timedelta
from datetime import datetime as dt
import datetime
import json
from altair import datum

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [98]:

#highlighting important NPIs in WA
data = {'date': [ "2020-03-23", "2020-06-01", "2020-11-18", "2021-02-14"], 'event':[ "Stay at home", "Stay at home lifted", "Closing restaurants", "Reopening restaurants"]}

npidf = pd.DataFrame(data)
npidf.date = pd.to_datetime(npidf.date)

rule = alt.Chart(npidf).mark_rule(
    color="black",
    strokeWidth=2, 
    opacity = 0.3
).encode(
    alt.X('date:T', axis=alt.Axis(title=None))
).properties(
    width=800,
    height=300
)

text = alt.Chart(npidf).mark_text(
    align='left',
    baseline='middle',
    dx=2,
    dy=-135,
    size=13
).encode(
    alt.X('date:T',axis=alt.Axis(title=None)),
    text='event',
    color=alt.value('#000000')
).properties(
    width=800,
    height=300
)

In [99]:
king_county_map = gpd.read_file('~/Desktop/gitrepos/seattle-geojson/king_county_geojsons/2016_king_county_pumas.geojson')
metadata = pd.read_csv("../data-files/mobility_income_hh.csv")
mobility = pd.read_csv("../data-files/total_normalized_mobility.csv")
pop = pd.read_csv("../data-files/population_by_puma.csv")

In [100]:
mobility

Unnamed: 0  start_date     poi_geo visitor_geo    sum_visits  \
0           420  2020-01-06  North King  North King  6.156223e+06   
1           424  2020-01-13  North King  North King  5.773170e+06   
2           428  2020-01-20  North King  North King  6.626474e+06   
3           432  2020-01-27  North King  North King  8.428190e+06   
4           436  2020-02-03  North King  North King  5.876076e+06   
..          ...         ...         ...         ...           ...   
223         859  2022-02-07  South King  South King  3.599757e+06   
224         863  2022-02-14  South King  South King  3.698613e+06   
225         867  2022-02-21  South King  South King  3.850547e+06   
226         871  2022-02-28  South King  South King  3.865952e+06   
227         875  2022-03-07  South King  South King  3.982987e+06   

         category  year  normalized_visits  
0    within North  2020           0.898154  
1    within North  2020           0.842269  
2    within North  2020           0.966760  
3    within North  2020           1.229619  
4    within North  2020           0.857282  
..            ...   ...                ...  
223  within South  2022           0.941334  
224  within South  2022           0.967185  
225  within South  2022           1.006915  
226  within South  2022           1.010944  
227  within South  2022           1.041548  

[228 rows x 8 columns]

In [101]:
mobility.rename(columns={'poi_geo': 'Region'}, inplace=True)
mobility.Region[mobility.Region == "North King"] = "North King County"
mobility.Region[mobility.Region == "South King"] = "South King County"

#mobility.normalized_visits = mobility.normalized_visits *100


/var/folders/h9/0347drb57tsgxzbddmvmlvf80000gp/T/ipykernel_26319/48067480.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mobility.Region[mobility.Region == "North King"] = "North King County"
/var/folders/h9/0347drb57tsgxzbddmvmlvf80000gp/T/ipykernel_26319/48067480.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  mobility.Region[mobility.Region == "South King"] = "South King County"


In [102]:
king_county_map.PUMACE10 = king_county_map.PUMACE10.astype("int")
metadata.PUMA = metadata.PUMA.astype("int")

In [103]:
metadata

Unnamed: 0   PUMA  median_income  household_size region  sum_essential  \
0            0  11601  113141.333333        2.103333    nKC    7909.666667   
1            1  11602   87583.333333        2.323333    nKC    7839.000000   
2            2  11603  117604.750000        1.660000    nKC    3362.888889   
3            3  11604   94083.750000        2.245000    nKC    8440.500000   
4            4  11605   89781.333333        2.218333    nKC    5295.666667   
5            5  11606  100738.857143        2.438000    nKC    7594.200000   
6            6  11607  124847.000000        2.436667    nKC    9123.000000   
7            7  11608  142123.666667        2.553333    nKC    4050.000000   
8            8  11609  167394.000000        2.810000    nKC    3882.250000   
9            9  11610   79519.500000        2.437500    sKC    7715.000000   
10          10  11611   73801.600000        2.600000    sKC    8188.400000   
11          11  11612   71858.000000        2.577500    sKC   11460.500000   
12          12  11613   77999.000000        2.872500    sKC   12717.250000   
13          13  11614   71000.333333        2.810000    sKC    8440.000000   
14          14  11615  106712.375000        2.720000    sKC    7614.125000   
15          15  11616  140064.000000        2.770000    nKC    2913.500000   

           total  percent_essential  
0   25951.000000           0.304767  
1   21526.000000           0.364164  
2   11926.444444           0.281905  
3   22544.250000           0.374379  
4   11683.000000           0.453223  
5   17706.600000           0.428894  
6   28516.666667           0.319926  
7   13223.166667           0.306285  
8   13814.500000           0.281019  
9   13845.750000           0.557241  
10  12683.600000           0.645589  
11  18392.000000           0.623097  
12  20532.000000           0.619375  
13  12284.333333           0.687073  
14  14889.500000           0.511384  
15   7668.625000           0.379890

In [104]:
metadata = metadata.merge(pop, left_on = "PUMA", right_on = "puma")

In [105]:
map_mobility = pd.merge(king_county_map, metadata, left_on ="PUMACE10", right_on = "PUMA")

In [106]:
map_mobility

STATEFP10  PUMACE10  GEOID10  \
0         53     11612  5311612   
1         53     11616  5311616   
2         53     11611  5311611   
3         53     11605  5311605   
4         53     11603  5311603   
5         53     11601  5311601   
6         53     11606  5311606   
7         53     11615  5311615   
8         53     11614  5311614   
9         53     11613  5311613   
10        53     11609  5311609   
11        53     11604  5311604   
12        53     11602  5311602   
13        53     11607  5311607   
14        53     11610  5311610   
15        53     11608  5311608   

                                           NAMELSAD10 MTFCC10 FUNCSTAT10  \
0   King County (Far Southwest)--Federal Way, Des ...   G6120          S   
1   King County (Northeast)--Snoqualmie City, Cott...   G6120          S   
2   King County (West Central)--Burien, SeaTac, Tu...   G6120          S   
3    Seattle City (West)--Duwamish & Beacon Hill PUMA   G6120          S   
4   Seattle City (Downtown)--Queen Anne & Magnolia...   G6120          S   
5                       Seattle City (Northwest) PUMA   G6120          S   
6   King County (Northwest)--Shoreline, Kenmore & ...   G6120          S   
7   King County (Southeast)--Maple Valley, Covingt...   G6120          S   
8   King County (Southwest)--Auburn City & Lakelan...   G6120          S   
9     King County (Southwest Central)--Kent City PUMA   G6120          S   
10  King County (Central)--Sammamish, Issaquah, Me...   G6120          S   
11        Seattle City (Southeast)--Capitol Hill PUMA   G6120          S   
12                      Seattle City (Northeast) PUMA   G6120          S   
13  King County (Northwest)--Redmond, Kirkland Cit...   G6120          S   
14  King County (Central)--Renton City, Fairwood, ...   G6120          S   
15  King County (Northwest Central)--Greater Belle...   G6120          S   

       ALAND10   AWATER10   INTPTLAT10    INTPTLON10  ...   PUMA  \
0    160787093  279511356  +47.4764315  -122.4271827  ...  11612   
1   2477877975   49614322  +47.5779171  -121.6433869  ...  11616   
2    104742959    6783935  +47.4500687  -122.3101564  ...  11611   
3     70127509   10095982  +47.5521279  -122.3523950  ...  11605   
4     29268443    8335378  +47.6391415  -122.3720415  ...  11603   
5     43424520    5974262  +47.6909932  -122.3619886  ...  11601   
6     75262645    5623251  +47.7564420  -122.2787890  ...  11606   
7   1704958484   21295646  +47.2986756  -121.7866429  ...  11615   
8    178265957    2448403  +47.2844346  -122.1690701  ...  11614   
9     96642411    1910059  +47.3879703  -122.2127275  ...  11613   
10   203389284   29361305  +47.5614826  -122.0700114  ...  11609   
11    34303404   19689584  +47.5814570  -122.2744307  ...  11604   
12    39488590   15926832  +47.6875388  -122.2847471  ...  11602   
13    93383747   11263416  +47.6827310  -122.1668045  ...  11607   
14    75934179    4676619  +47.4836108  -122.1904418  ...  11610   
15    91511410   24462626  +47.6070945  -122.1644100  ...  11608   

    median_income  household_size  region  sum_essential         total  \
0    71858.000000        2.577500     sKC   11460.500000  18392.000000   
1   140064.000000        2.770000     nKC    2913.500000   7668.625000   
2    73801.600000        2.600000     sKC    8188.400000  12683.600000   
3    89781.333333        2.218333     nKC    5295.666667  11683.000000   
4   117604.750000        1.660000     nKC    3362.888889  11926.444444   
5   113141.333333        2.103333     nKC    7909.666667  25951.000000   
6   100738.857143        2.438000     nKC    7594.200000  17706.600000   
7   106712.375000        2.720000     sKC    7614.125000  14889.500000   
8    71000.333333        2.810000     sKC    8440.000000  12284.333333   
9    77999.000000        2.872500     sKC   12717.250000  20532.000000   
10  167394.000000        2.810000     nKC    3882.250000  13814.500000   
11   94083.750000        2.245000     nKC    8440.500000  22544.25000

In [107]:
map_mobility.region[map_mobility.region == "nKC"] = "North King County"
map_mobility.region[map_mobility.region == "sKC"] = "South King County"

kc_map = alt.Chart(map_mobility).mark_geoshape(
        stroke='black', strokeWidth = 1
    ).encode(
        alt.Color("region:N")).properties(
    width=150,
    height=150
) 

kc_map.save("king_county_region_map.html")
kc_map

/var/folders/h9/0347drb57tsgxzbddmvmlvf80000gp/T/ipykernel_26319/100806084.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  map_mobility.region[map_mobility.region == "nKC"] = "North King County"
/var/folders/h9/0347drb57tsgxzbddmvmlvf80000gp/T/ipykernel_26319/100806084.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  map_mobility.region[map_mobility.region == "sKC"] = "South King County"


alt.Chart(...)

In [108]:
only_region = map_mobility[["region", "geometry"]]
region_outline = only_region.dissolve(by='region')


In [109]:
outline_graph = alt.Chart(region_outline).mark_geoshape(fill=None, 
        stroke='black', strokeWidth = 4
    ).properties(
    width=150,
    height=150
) 
outline_graph

alt.Chart(...)

In [110]:
    # Add Choropleth Layer
hh = alt.Chart(map_mobility, title = "2020-2015 Average Household Size").mark_geoshape(
        stroke='black'
    ).encode(
        alt.Color("household_size:Q", title = "Average Household Size", legend=alt.Legend(orient = "right", columns = 2, titleAlign = "center", titleOrient = "right",titleFontSize = 14, labelAlign = "right"))).properties(
    width=200,
    height=200
)   
hh_map = hh + outline_graph

In [111]:
    # Add Choropleth Layer
pop_map = alt.Chart(map_mobility, title = "2021 Population Size").mark_geoshape(
        stroke='black'
    ).encode(
        alt.Color("Total Population", title = "Population Size", legend=alt.Legend(orient = "right", columns = 2, titleAlign = "center", titleOrient = "right",titleFontSize = 14, labelAlign = "right"))).properties(
    width=200,
    height=200
)   
pop_map_final = pop_map + outline_graph
pop_map_final

alt.LayerChart(...)

In [112]:
    # Add Choropleth Layer
income = alt.Chart(map_mobility, title = "2020 Median Household Income").mark_geoshape(
        stroke='black'
    ).encode(
        alt.Color("median_income:Q", title = " Median Income (in US dollars)", legend=alt.Legend(orient = "right", columns = 2, titleAlign = "center", titleOrient = "right",titleFontSize = 11, labelAlign = "right"))).properties(
    width=200,
    height=200
)   

In [113]:
income_map = income + outline_graph

In [114]:
    # Add Choropleth Layer
    essential = alt.Chart(map_mobility, title = "Percent essential worker 2015-2020").mark_geoshape(
        stroke='black'
    ).encode(
        alt.Color("percent_essential:Q", title = "Percent Essential Worker", legend=alt.Legend(orient = "right", columns = 2, titleAlign = "center", titleOrient = "right",titleFontSize = 14, labelAlign = "right") )).properties(
    width=200,
    height=200
)   
essential_map = essential + outline_graph

In [115]:
maps = alt.hconcat(income_map , essential_map, hh_map, pop_map_final).resolve_scale(color = "independent")
maps

alt.HConcatChart(...)

In [116]:
mob_plot =  alt.Chart(mobility, width = 750).mark_line(interpolate='monotone', opacity = 1.0).encode(
    x=alt.X('start_date:T', axis=alt.Axis(title=None, grid=False, format="%B %Y")),
    y=alt.Y('normalized_visits:Q',axis=alt.Axis(title="Percent Change in Mobility Compared to 2019", grid=False, format = "%")),
    color = alt.Color("Region:N", legend=alt.Legend(offset = -200,  labelFontSize = 18, titleFontSize = 18))).properties(
    width=1175,
    height=300
)
line = alt.Chart(pd.DataFrame({'y': [1.0]})).mark_rule(strokeDash=[1,1]).encode(y='y')

In [117]:
mob_plot

alt.Chart(...)

In [180]:
#making background shading to represent different variants
cutoff = pd.DataFrame({
     "variant" : ["Non-VOC", "Alpha", "Delta", "Omicron"],
    'start': ["2020-01-01","2020-10-01", "2021-04-01", "2021-12-01"],
    'stop': ["2020-10-01","2021-04-01", "2021-12-01", "2022-03-8"],
})

areas = alt.Chart(
    cutoff.reset_index()
).mark_rect(
    opacity=0.1
).encode(
    x='start:T',
    x2='stop:T',
    y=alt.value(0),  # pixels from top
    y2=alt.value(300),  # pixels from top
    color=alt.Color('variant:N', scale = alt.Scale(scheme= "set1"), legend = None )
)
areas

alt.Chart(...)

In [181]:
mob = mob_plot + line + areas

In [182]:
mob.resolve_scale(color = "independent")

alt.LayerChart(...)

In [120]:
# Add labels to each chart
mob = mob.properties(title='A')
income_map = income_map.properties(title='B')
essential_map = essential_map.properties(title='C')
hh_map = hh_map.properties(title='D')
pop_map_final = pop_map_final.properties(title= "E")

# Concatenate labeled charts A and B horizontally
maps = alt.hconcat(income_map , essential_map, hh_map, pop_map_final).resolve_scale(color = "independent")

# Concatenate labeled charts AB and CD vertically
chart_abcd_labeled = alt.vconcat(mob, maps, spacing=50)#.resolve_scale(x='shared', color ='shared')

chart_abcd_labeled.configure_view(
    strokeWidth=0
).configure_title(
    anchor='start', fontSize= 30
).configure_axis(
    labelFontSize=14,
    titleFontSize=14
).configure_legend(
    labelFontSize = 14)

alt.VConcatChart(...)

In [121]:
figure6 = (mob & maps).configure_axis(
    labelFontSize=14,
    titleFontSize=14
)
figure6

alt.VConcatChart(...)

In [122]:
figure6.save("figure6.html")